In [0]:
# set whether normal process or being run by Elsevier supporters
permissions='fulldata' # default or fulldata
# set the project name
project_name = 'test_project_1'  # This is the folder name that you work in, e.g. 'test_project_1'

In [0]:
%run /Snippets/header_008

PROJECT DETAILS:
Project identifier: test_project_1
Cluster data access level: fulldata


EXECUTION DETAILS:
Spark version: 11.3.x-scala2.12, 
Cluster Node Type: i3.xlarge, 
Driver Node Type: c4.2xlarge, 
Worker Node Type: i3.xlarge


DATA SNAPSHOT DETAILS:
This notebook uses the latest snapshot date for this version: "v008.20221021151538/", (21 October 2022)

 The following are the Scopus snapshot dates available for datasets at v008:
['v008.20220314092239/', 'v008.20220906063204/', 'v008.20221021151538/']
(If you want to use a different snapshot, in the first cell of your notebook, set the variable `custom_snapshot_date` to one of the options listed above (string data type))



DATA SAMPLE DETAILS:
Setting paths to run on full datasets (100% Scopus publication volume)


In [0]:
import pandas as pd
import numpy as np
import pyspark.pandas as ps
from pyspark.sql import SparkSession
from pyspark.sql.window import Window
from pyspark.sql.functions import monotonically_increasing_id, row_number, coalesce, countDistinct

In [0]:
# load the datasets
#df_ani = spark.read.format("parquet").load(basePath + tablename_ani)
# EID(long), Year(int), DOI
# Af.affiliation_ids: .select(func.col('Au.email_sha1'))

df_ipr = spark.read.format("parquet").load(basePath + tablename_ipr)
# afid, preferred_name, org_type, postal_code, city, state, country, country_tag

#df_smc_ani = spark.read.format("parquet").load(basePath+tablename_smc_complete)
# EID, subfield_article, subfield_hybrid, subfield_journal

in this notebook, use parent data of affiliation in df-ipr to get the final parent of each affiliation
(here the parent means the affiliation belong to another, like the department of the university)

In [0]:
af_data = df_ipr.filter(df_ipr.country_tag=='usa')
af_data = af_data.withColumn('key',func.col('afid'))
#display(af_data)
af_data.count()

Out[9]: 2529287

In [0]:
#count distinct in parent
af_data.select(countDistinct('parent')).show()

+----------------------+
|count(DISTINCT parent)|
+----------------------+
|                245583|
+----------------------+



In [0]:
# if one affiliation has no parent, use itself as the parent
af_data_1 = af_data.withColumn('parent',coalesce('parent', 'afid')).withColumn('parent_preferred_name',coalesce('parent_preferred_name', 'preferred_name'))
af_data_1 = af_data_1.withColumn('key',func.col('parent'))
#display(af_data_1)

In [0]:
# count distinct parent, since some affilation's parent is filled as itself, it's heavily increased
af_data_1.select(countDistinct('parent')).show()

+----------------------+
|count(DISTINCT parent)|
+----------------------+
|                990784|
+----------------------+



In [0]:
#combine son-parent-parent's parent fisrt time (in order to get the final parent)
merge = af_data_1.join(af_data,'key')
display(merge)

key afid preferred_name sort_name address_part postal_code city state country country_tag name_variant org_domain org_type parent parent_preferred_name afid preferred_name sort_name address_part postal_code city state country country_tag name_variant org_domain org_type parent parent_preferred_name 60000027 103035115 EBI Division EBI Division Three Technology Drive 95035-7916 Milpitas CA United States usa null kla-tencor.com null 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 12)) kla-tencor.com comp null null 60000027 125865588 EEP Group EEP Group Three Technology Drive 95035-7916 Milpitas CA United States usa null kla-tencor.com null 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 12)) kla-tencor.com comp null null 60000027 107099789 Process Control Information Division Process Control Information Division Three Technology Drive 95035-7916 Milpitas CA United States usa null kla-tencor.com null 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 12)) kla-tencor.com comp null null 60000027 103035114 Film Measurement Division Film Measurement Division Three Technology Drive 95035-7916 Milpitas CA United States usa null kla-tencor.com null 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 12)) kla-tencor.com comp null null 60000027 125865724 Mie Service Center Mie Service Center Three Technology Drive 95035-7916 Milpitas CA United States usa null kla-tencor.com null 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 

In [0]:
#reserve the son-parent's parent afid data
af_parent_list = af_data_1.select('afid','preferred_name', 'parent', 'parent_preferred_name')
af_parent_left_0 = af_parent_list.withColumn('key',func.col('parent'))
display(af_parent_left_0)

afid preferred_name parent parent_preferred_name key 112781415 Department of Health Promotion Sciences 101366452 UOHSC 101366452 125369330 Cardiovascular Division 60024609 Indiana University-Purdue University Indianapolis 60024609 122345448 Headache Care Centre 100370811 Primary Care Network 100370811 118085370 Director of the Environmental Studies Program 60023004 University of Delaware 60023004 119696230 The Voice of the Patient, Inc 119696230 The Voice of the Patient, Inc 119696230 101131800 Fontana Center 101131800 Fontana Center 101131800 60101239 Bally Total Fitness Corporation 60101239 Bally Total Fitness Corporation 60101239 119020353 Department of Critical Care Medicine 116431064 University Medical Center Phoenix 116431064 116212568 Clinical Social Worker 100523716 Mid East. Iowa Commun. Ment. Hlth Cent. 100523716 108024004 Cardiovascular Disease Program 60028095 Rosalind Franklin University of Medicine and Science 60028095 103568574 Department of Molecular Biophysics 60010374 Medical College of Virginia 60010374 110125384 Columbiana Cardiovascular Consultants 110125384 Columbiana Cardiovascular Consultants 110125384 113980083 Center for Digital Archaeology (CoDA) 60025038 University of California, Berkeley 60025038 117855622 Department of Intercollegiate Athletics 60005170 Wagner College 60005170 103373293 Division of Biologic Basis of Disease 60006577 National Institutes of Health (NIH) 60006577 101854069 Consultation and Evaluation Services 101854069 Consultation and Evaluation Services 101854069 119033768 Division of Rheumatology 106566882 Minneapolis Veterans Affairs Health Care System 106566882 110785552 Department of Internal Medicine 60008724 Duke University 60008724 100742370 L.L.C. 100742370 L.L.C. 100742370 115537253 INSPIRE Research Institute for Pre-College Engineering 60009254 Purdue University 60009254 121574606 Department of Emergency Medicine 60007355 Phoenix Indian Medical Center 60007355 128222204 UK Center on Trauma and Children 128222204 UK Center on Trauma and Children 128222204 113319945 Department of Epidemiology 60028124 WVU Health Sciences Center Morgantown 60028124 112559901 Department of Mechanical Engineering and Technology 60103974 Wentworth Institute of Technology 60103974 100544556 Acupuncture Clinic of Missoula 100544556 Acupuncture Clinic of Missoula 100544556 107968293 Department of Marketing and Logistics 107860378 University of North 107860378 108238284 Department of Immunology and Rheumatology 60021519 University of Miami Leonard M. Miller School of Medicine 60021519 117493739 Knobles Scientific and Analysis 117493739 Knobles Scientific and Analysis 117493739 116639963 Illinois Institute 106027754 Institute of Technology 106027754 101417435 Pacific Plastic Technology, Inc. 101417435 Pacific Plastic Technology, Inc. 101417435 119121508 Center for Breast Care 60077414 The University of Toledo Medical Center 60077414 106818517 Hughes Aircraft Co. Tech. Support Div.-EDSG 60005304 Raytheon 60005304 105990174 Anaborex, Inc. 105990174 Anaborex, Inc. 105990174 123001658 CBER/FDA 123001658 CBER/FDA 123001658 114108636 Pediatric Endocrinology 60007200 Michigan Medicine 60007200 119930160 Division for Toxicology 119930160 Division for Toxicology 119930160 118011631 University of Technology of Troyes ICD-CREIDD UMR 6281 Troyes France 118011631 University of Technology of Troyes ICD-CREIDD UMR 6281 Troyes France 118011631 120631055 Hines Academic Center 112 60030452 Texas State University 60030452 103967413 Division of Hematology/Oncolgy 60018917 The Brody School of Medicine 60018917 109009483 Departments of Preclinical Therapeutics, Regulatory Affairs and Nonclinical Development 60027014 Seattle Genetics, Inc. 60027014 104201176 Division of Hematoiogy-Oneology 60023691 University of California, San Francisco 60023691 113186867 Department of Neuroen-teric Clinical 105869736 The Research Group 105869736 127318062 Department of Biostatistics and Epidemiology 60022783 West Virginia University Sch

In [0]:
af_parent_left_0.select(countDistinct('parent')).show()

+----------------------+
|count(DISTINCT parent)|
+----------------------+
|                990784|
+----------------------+



In [0]:
af_parent_target = af_parent_list.withColumn('key',func.col('afid'))
af_parent_target = af_parent_target.withColumnRenamed("afid",'afid_target').withColumnRenamed("preferred_name",'preferred_name_target').withColumnRenamed("parent",'parent_target').withColumnRenamed("parent_preferred_name",'parent_preferred_name_target')
display(af_parent_target)

afid_target preferred_name_target parent_target parent_preferred_name_target key 112781415 Department of Health Promotion Sciences 101366452 UOHSC 112781415 125369330 Cardiovascular Division 60024609 Indiana University-Purdue University Indianapolis 125369330 122345448 Headache Care Centre 100370811 Primary Care Network 122345448 118085370 Director of the Environmental Studies Program 60023004 University of Delaware 118085370 119696230 The Voice of the Patient, Inc 119696230 The Voice of the Patient, Inc 119696230 101131800 Fontana Center 101131800 Fontana Center 101131800 60101239 Bally Total Fitness Corporation 60101239 Bally Total Fitness Corporation 60101239 119020353 Department of Critical Care Medicine 116431064 University Medical Center Phoenix 119020353 116212568 Clinical Social Worker 100523716 Mid East. Iowa Commun. Ment. Hlth Cent. 116212568 108024004 Cardiovascular Disease Program 60028095 Rosalind Franklin University of Medicine and Science 108024004 103568574 Department of Molecular Biophysics 60010374 Medical College of Virginia 103568574 110125384 Columbiana Cardiovascular Consultants 110125384 Columbiana Cardiovascular Consultants 110125384 113980083 Center for Digital Archaeology (CoDA) 60025038 University of California, Berkeley 113980083 117855622 Department of Intercollegiate Athletics 60005170 Wagner College 117855622 103373293 Division of Biologic Basis of Disease 60006577 National Institutes of Health (NIH) 103373293 101854069 Consultation and Evaluation Services 101854069 Consultation and Evaluation Services 101854069 119033768 Division of Rheumatology 106566882 Minneapolis Veterans Affairs Health Care System 119033768 110785552 Department of Internal Medicine 60008724 Duke University 110785552 100742370 L.L.C. 100742370 L.L.C. 100742370 115537253 INSPIRE Research Institute for Pre-College Engineering 60009254 Purdue University 115537253 121574606 Department of Emergency Medicine 60007355 Phoenix Indian Medical Center 121574606 128222204 UK Center on Trauma and Children 128222204 UK Center on Trauma and Children 128222204 113319945 Department of Epidemiology 60028124 WVU Health Sciences Center Morgantown 113319945 112559901 Department of Mechanical Engineering and Technology 60103974 Wentworth Institute of Technology 112559901 100544556 Acupuncture Clinic of Missoula 100544556 Acupuncture Clinic of Missoula 100544556 107968293 Department of Marketing and Logistics 107860378 University of North 107968293 108238284 Department of Immunology and Rheumatology 60021519 University of Miami Leonard M. Miller School of Medicine 108238284 117493739 Knobles Scientific and Analysis 117493739 Knobles Scientific and Analysis 117493739 116639963 Illinois Institute 106027754 Institute of Technology 116639963 101417435 Pacific Plastic Technology, Inc. 101417435 Pacific Plastic Technology, Inc. 101417435 119121508 Center for Breast Care 60077414 The University of Toledo Medical Center 119121508 106818517 Hughes Aircraft Co. Tech. Support Div.-EDSG 60005304 Raytheon 106818517 105990174 Anaborex, Inc. 105990174 Anaborex, Inc. 105990174 123001658 CBER/FDA 123001658 CBER/FDA 123001658 114108636 Pediatric Endocrinology 60007200 Michigan Medicine 114108636 119930160 Division for Toxicology 119930160 Division for Toxicology 119930160 118011631 University of Technology of Troyes ICD-CREIDD UMR 6281 Troyes France 118011631 University of Technology of Troyes ICD-CREIDD UMR 6281 Troyes France 118011631 120631055 Hines Academic Center 112 60030452 Texas State University 120631055 103967413 Division of Hematology/Oncolgy 60018917 The Brody School of Medicine 103967413 109009483 Departments of Preclinical Therapeutics, Regulatory Affairs and Nonclinical Development 60027014 Seattle Genetics, Inc. 109009483 104201176 Division of Hematoiogy-Oneology 60023691 University of California, San Francisco 104201176 113186867 Department of Neuroen-teric Clinical 105869736 The Research Group 113186867 127318062 Department of Biostatistics and Ep

In [0]:
merge_1 = af_parent_left_0.join(af_parent_target,'key','left')
display(merge_1)

key afid preferred_name parent parent_preferred_name afid_target preferred_name_target parent_target parent_preferred_name_target 60000027 125865887 Marketing Division 60000027 KLA Corporation 60000027 KLA Corporation 60000027 KLA Corporation 60000071 126071145 Department of World Languages 60000071 Calvin University 60000071 Calvin University 60000071 Calvin University 60000102 113319358 Undergraduate Biology 60000102 Fisk University 60000102 Fisk University 60000102 Fisk University 60000149 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000209 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 103046610 Surgical Research Center 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 109518014 Department of Pediatrics 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 103046880 Section of Endocrinology (CDM) 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000221 121432388 Department of Orthopaedics UC Denver 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047608 Marion Downs Hearing Center 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 117057435 Department of Engineering News-Record Enterprise-Online 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 116354919 NOAA Environmental Technology Laboratory 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047475 Berkeley Research Associates and Department of Astrophysical, Planetary and Atmospheric Sciences 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 116580250 Department of Anesthesiology and Organ Protection Program 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047221 Colorado Power Electronics Center 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047826 Department of Preventive Medicine and Biometrics 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 120503511 Center for Spine and Orthopedics 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047520 Institute for Behavioral Genetics 447 UCB 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000247 113503958 Pharmacology Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 113450548 Immunology and Microbial Pathogenesis Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000278 106666235 Texas Children's Hospital 60000278 Ben Taub General Hospital 60000278 Ben Taub General Hospital 60000278 Ben Taub General Hospital 60000372 115872892 Departments of medicine and pathology 60000372 Bergen Pines County Hospital

In [0]:
af_parent_left_1 = merge_1.select('afid','preferred_name','parent_target','parent_preferred_name_target')
af_parent_left_1 = af_parent_left_1.withColumnRenamed("parent_target",'parent').withColumnRenamed("parent_preferred_name_target",'parent_preferred_name').withColumn('key',func.col('parent'))
display(af_parent_left_1)

afid preferred_name parent parent_preferred_name key 125865887 Marketing Division 60000027 KLA Corporation 60000027 126071145 Department of World Languages 60000071 Calvin University 60000071 113319358 Undergraduate Biology 60000102 Fisk University 60000102 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 103046610 Surgical Research Center 60000209 UConn Health 60000209 109518014 Department of Pediatrics 60000209 UConn Health 60000209 103046880 Section of Endocrinology (CDM) 60000209 UConn Health 60000209 121432388 Department of Orthopaedics UC Denver 60000221 University of Colorado Boulder 60000221 103047608 Marion Downs Hearing Center 60000221 University of Colorado Boulder 60000221 117057435 Department of Engineering News-Record Enterprise-Online 60000221 University of Colorado Boulder 60000221 116354919 NOAA Environmental Technology Laboratory 60000221 University of Colorado Boulder 60000221 103047475 Berkeley Research Associates and Department of Astrophysical, Planetary and Atmospheric Sciences 60000221 University of Colorado Boulder 60000221 116580250 Department of Anesthesiology and Organ Protection Program 60000221 University of Colorado Boulder 60000221 103047221 Colorado Power Electronics Center 60000221 University of Colorado Boulder 60000221 103047826 Department of Preventive Medicine and Biometrics 60000221 University of Colorado Boulder 60000221 120503511 Center for Spine and Orthopedics 60000221 University of Colorado Boulder 60000221 103047520 Institute for Behavioral Genetics 447 UCB 60000221 University of Colorado Boulder 60000221 113503958 Pharmacology Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 113450548 Immunology and Microbial Pathogenesis Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 106666235 Texas Children's Hospital 60000278 Ben Taub General Hospital 60000278 115872892 Departments of medicine and pathology 60000372 Bergen Pines County Hospital 60000372 122694538 SRI Education 60000461 SRI International 60000461 103060754 Aeronomy Program 60000461 SRI International 60000461 116963509 Center for Science, Technology, and Economic Development 60000461 SRI International 60000461 103065376 Infection Control Department 60000550 St. Luke's Hospital Bethlehem 60000550 116881432 Division of N. American Rockwell 60000716 United Technologies Corporation 60000716 109418760 Facilities Engineering Division 60000854 NASA Langley Research Center 60000854 118818265 Craig Technologies Inc 60000854 NASA Langley Research Center 60000854 109418784 Applied Technologies and Testing Branch 60000854 NASA Langley Research Center 60000854 103084007 College of Aviation 60000879 Western Michigan University 60000879 123645584 Socio-Cultural Studies 60000879 Western Michigan University 60000879 124068496 Center for Printing and Coating Research 60000879 Western Michigan University 60000879 124393599 Distribution Operations 60000939 Caterpillar Inc. 60000939 124584749 Program in Colorectal Cancer 60000948 School of Medicine 60000948 103092513 General Clinical Research Center 60000948 School of Medicine 60000948 114164695 Brain Tumor Research Center 60001001 Broad Institute 60001001 103098988 Department of Civil Engineering 60001032 Carnegie Institute of Technology 60001032 126651123 Department of Lead Evaluation 60001149 Bristol-Myers Squibb Research and Development 60001149 60001213 Vermont Institute Natural Science 60001213 Vermont Institute Natural Science 60001213 118164821 Government Relations 60001227 American Dietetic Association 60001227 103107258 Commission on Dietetic Registration 60001227 American Dietetic Association 60001227 124592031 Microbiology Section 60001383 Sa

In [0]:
# count distinct again to check how many parent disappear due to code above
af_parent_left_1.select(countDistinct('parent')).show()

+----------------------+
|count(DISTINCT parent)|
+----------------------+
|                990664|
+----------------------+



In [0]:
merge_2 = af_parent_left_1.join(af_parent_target,'key','left')
display(merge_2)

key afid preferred_name parent parent_preferred_name afid_target preferred_name_target parent_target parent_preferred_name_target 60000027 125865887 Marketing Division 60000027 KLA Corporation 60000027 KLA Corporation 60000027 KLA Corporation 60000071 126071145 Department of World Languages 60000071 Calvin University 60000071 Calvin University 60000071 Calvin University 60000102 113319358 Undergraduate Biology 60000102 Fisk University 60000102 Fisk University 60000102 Fisk University 60000149 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester 60000209 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 103046610 Surgical Research Center 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 109518014 Department of Pediatrics 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000209 103046880 Section of Endocrinology (CDM) 60000209 UConn Health 60000209 UConn Health 60000209 UConn Health 60000221 121432388 Department of Orthopaedics UC Denver 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047608 Marion Downs Hearing Center 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 117057435 Department of Engineering News-Record Enterprise-Online 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 116354919 NOAA Environmental Technology Laboratory 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047475 Berkeley Research Associates and Department of Astrophysical, Planetary and Atmospheric Sciences 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 116580250 Department of Anesthesiology and Organ Protection Program 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047221 Colorado Power Electronics Center 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047826 Department of Preventive Medicine and Biometrics 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 120503511 Center for Spine and Orthopedics 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 103047520 Institute for Behavioral Genetics 447 UCB 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000221 University of Colorado Boulder 60000247 113503958 Pharmacology Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 113450548 Immunology and Microbial Pathogenesis Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 Weill Cornell Graduate School of Medical Sciences 60000278 106666235 Texas Children's Hospital 60000278 Ben Taub General Hospital 60000278 Ben Taub General Hospital 60000278 Ben Taub General Hospital 60000372 115872892 Departments of medicine and pathology 60000372 Bergen Pines County Hospital

In [0]:
af_parent_left_2 = merge_2.select('afid','preferred_name','parent_target','parent_preferred_name_target')
af_parent_left_2 = af_parent_left_2.withColumnRenamed("parent_target",'parent').withColumnRenamed("parent_preferred_name_target",'parent_preferred_name').withColumn('key',func.col('parent'))
display(af_parent_left_2)

afid preferred_name parent parent_preferred_name key 125865887 Marketing Division 60000027 KLA Corporation 60000027 126071145 Department of World Languages 60000071 Calvin University 60000071 113319358 Undergraduate Biology 60000102 Fisk University 60000102 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 103046610 Surgical Research Center 60000209 UConn Health 60000209 109518014 Department of Pediatrics 60000209 UConn Health 60000209 103046880 Section of Endocrinology (CDM) 60000209 UConn Health 60000209 121432388 Department of Orthopaedics UC Denver 60000221 University of Colorado Boulder 60000221 103047608 Marion Downs Hearing Center 60000221 University of Colorado Boulder 60000221 117057435 Department of Engineering News-Record Enterprise-Online 60000221 University of Colorado Boulder 60000221 116354919 NOAA Environmental Technology Laboratory 60000221 University of Colorado Boulder 60000221 103047475 Berkeley Research Associates and Department of Astrophysical, Planetary and Atmospheric Sciences 60000221 University of Colorado Boulder 60000221 116580250 Department of Anesthesiology and Organ Protection Program 60000221 University of Colorado Boulder 60000221 103047221 Colorado Power Electronics Center 60000221 University of Colorado Boulder 60000221 103047826 Department of Preventive Medicine and Biometrics 60000221 University of Colorado Boulder 60000221 120503511 Center for Spine and Orthopedics 60000221 University of Colorado Boulder 60000221 103047520 Institute for Behavioral Genetics 447 UCB 60000221 University of Colorado Boulder 60000221 113503958 Pharmacology Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 113450548 Immunology and Microbial Pathogenesis Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 106666235 Texas Children's Hospital 60000278 Ben Taub General Hospital 60000278 115872892 Departments of medicine and pathology 60000372 Bergen Pines County Hospital 60000372 122694538 SRI Education 60000461 SRI International 60000461 103060754 Aeronomy Program 60000461 SRI International 60000461 116963509 Center for Science, Technology, and Economic Development 60000461 SRI International 60000461 103065376 Infection Control Department 60000550 St. Luke's Hospital Bethlehem 60000550 116881432 Division of N. American Rockwell 60000716 United Technologies Corporation 60000716 109418760 Facilities Engineering Division 60000854 NASA Langley Research Center 60000854 118818265 Craig Technologies Inc 60000854 NASA Langley Research Center 60000854 109418784 Applied Technologies and Testing Branch 60000854 NASA Langley Research Center 60000854 103084007 College of Aviation 60000879 Western Michigan University 60000879 123645584 Socio-Cultural Studies 60000879 Western Michigan University 60000879 124068496 Center for Printing and Coating Research 60000879 Western Michigan University 60000879 124393599 Distribution Operations 60000939 Caterpillar Inc. 60000939 124584749 Program in Colorectal Cancer 60000948 School of Medicine 60000948 103092513 General Clinical Research Center 60000948 School of Medicine 60000948 114164695 Brain Tumor Research Center 60001001 Broad Institute 60001001 103098988 Department of Civil Engineering 60001032 Carnegie Institute of Technology 60001032 126651123 Department of Lead Evaluation 60001149 Bristol-Myers Squibb Research and Development 60001149 60001213 Vermont Institute Natural Science 60001213 Vermont Institute Natural Science 60001213 118164821 Government Relations 60001227 American Dietetic Association 60001227 103107258 Commission on Dietetic Registration 60001227 American Dietetic Association 60001227 124592031 Microbiology Section 60001383 Sa

In [0]:
#this time the distinct number is same with above, thus the parents are all final parent
af_parent_left_2.select(countDistinct('parent')).show()

+----------------------+
|count(DISTINCT parent)|
+----------------------+
|                990664|
+----------------------+



In [0]:
#get the final parent afid and get the information of final parent
af_parent_final = af_parent_left_2.withColumnRenamed("afid",'afid_final').withColumnRenamed("preferred_name",'preferred_name_final').withColumnRenamed("parent",'parent_final').withColumnRenamed("parent_preferred_name",'parent_preferred_name_final')
display(af_parent_final)

afid_final preferred_name_final parent_final parent_preferred_name_final key 125865887 Marketing Division 60000027 KLA Corporation 60000027 126071145 Department of World Languages 60000071 Calvin University 60000071 113319358 Undergraduate Biology 60000102 Fisk University 60000102 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 103046610 Surgical Research Center 60000209 UConn Health 60000209 109518014 Department of Pediatrics 60000209 UConn Health 60000209 103046880 Section of Endocrinology (CDM) 60000209 UConn Health 60000209 121432388 Department of Orthopaedics UC Denver 60000221 University of Colorado Boulder 60000221 103047608 Marion Downs Hearing Center 60000221 University of Colorado Boulder 60000221 117057435 Department of Engineering News-Record Enterprise-Online 60000221 University of Colorado Boulder 60000221 116354919 NOAA Environmental Technology Laboratory 60000221 University of Colorado Boulder 60000221 103047475 Berkeley Research Associates and Department of Astrophysical, Planetary and Atmospheric Sciences 60000221 University of Colorado Boulder 60000221 116580250 Department of Anesthesiology and Organ Protection Program 60000221 University of Colorado Boulder 60000221 103047221 Colorado Power Electronics Center 60000221 University of Colorado Boulder 60000221 103047826 Department of Preventive Medicine and Biometrics 60000221 University of Colorado Boulder 60000221 120503511 Center for Spine and Orthopedics 60000221 University of Colorado Boulder 60000221 103047520 Institute for Behavioral Genetics 447 UCB 60000221 University of Colorado Boulder 60000221 113503958 Pharmacology Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 113450548 Immunology and Microbial Pathogenesis Program 60000247 Weill Cornell Graduate School of Medical Sciences 60000247 106666235 Texas Children's Hospital 60000278 Ben Taub General Hospital 60000278 115872892 Departments of medicine and pathology 60000372 Bergen Pines County Hospital 60000372 122694538 SRI Education 60000461 SRI International 60000461 103060754 Aeronomy Program 60000461 SRI International 60000461 116963509 Center for Science, Technology, and Economic Development 60000461 SRI International 60000461 103065376 Infection Control Department 60000550 St. Luke's Hospital Bethlehem 60000550 116881432 Division of N. American Rockwell 60000716 United Technologies Corporation 60000716 109418760 Facilities Engineering Division 60000854 NASA Langley Research Center 60000854 118818265 Craig Technologies Inc 60000854 NASA Langley Research Center 60000854 109418784 Applied Technologies and Testing Branch 60000854 NASA Langley Research Center 60000854 103084007 College of Aviation 60000879 Western Michigan University 60000879 123645584 Socio-Cultural Studies 60000879 Western Michigan University 60000879 124068496 Center for Printing and Coating Research 60000879 Western Michigan University 60000879 124393599 Distribution Operations 60000939 Caterpillar Inc. 60000939 124584749 Program in Colorectal Cancer 60000948 School of Medicine 60000948 103092513 General Clinical Research Center 60000948 School of Medicine 60000948 114164695 Brain Tumor Research Center 60001001 Broad Institute 60001001 103098988 Department of Civil Engineering 60001032 Carnegie Institute of Technology 60001032 126651123 Department of Lead Evaluation 60001149 Bristol-Myers Squibb Research and Development 60001149 60001213 Vermont Institute Natural Science 60001213 Vermont Institute Natural Science 60001213 118164821 Government Relations 60001227 American Dietetic Association 60001227 103107258 Commission on Dietetic Registration 60001227 American Dietetic Association 60001227 124592031 Microbio

In [0]:
merge_final = af_parent_final.join(af_data,'key','left')
display(merge_final)

key afid_final preferred_name_final parent_final parent_preferred_name_final afid preferred_name sort_name address_part postal_code city state country country_tag name_variant org_domain org_type parent parent_preferred_name 60000027 125865887 Marketing Division 60000027 KLA Corporation 60000027 KLA Corporation KLA Corporation Three Technology Drive 95035-7916 Milpitas CA United States usa List(List(Kla-tencor Corporation, 751), List(Kla-tencor, 463), List(Kla-tencor Corp., 214), List(Kla Corporation, 131), List(Kla-tencor Corp, 93), List(Kla Tencor, 43), List(Kla-tencor Gmbh, 25), List(Kla-tencor Japan Ltd., 21), List(Kla Instruments Corporation, 19), List(Kla Corp., 19), List(Tencor Instruments, 18), List(Kla-tencor Corporation (israel), 14), List(Kla Instruments, 14), List(Kla, 13), List(Kla Instruments Corp., 12)) kla-tencor.com comp null null 60000071 126071145 Department of World Languages 60000071 Calvin University 60000071 Calvin University Calvin University 3201 Burton Street, S.E. 49546-4301 Grand Rapids MI United States usa List(List(Calvin College, 2339), List(Calvin University, 249), List(Calvin Coll, 23), List(Calvin Coll., 22)) calvin.edu univ null null 60000102 113319358 Undergraduate Biology 60000102 Fisk University 60000102 Fisk University Fisk University 1000 Seventeenth Avenue North 37208-3051 Nashville TN United States usa List(List(Fisk University, 1732), List(Fisk Univ, 70), List(Department Of Physics, 67), List(Fisk Univ., 15)) fisk.edu univ null null 60000149 124353304 Division of Surgery 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester Minnesota Rochester, University of 855 30th Ave SE 55904 Rochester MN United States usa List(List(University Of Minnesota, 659), List(Graduate School Of The University Of Minnesota, 252), List(Univ. Minnesota, 175), List(University Of Minnesota Rochester, 91), List(University Of Minnesota-rochester, 25), List(Is A Part Of The Graduate School Of The University Of Minnesota, 21), List(The Mayo Foundation Is A Part Of The Graduate School Of The University Of Minnesota, 20), List(The University Of Minnesota., 10), List(The University Of Minnesota, 10), List((university Of Minnesota), 9)) r.umn.edu univ null null 60000149 124324764 Department of Ophthalmology and Visual Neurosciences 60000149 University of Minnesota Rochester 60000149 University of Minnesota Rochester Minnesota Rochester, University of 855 30th Ave SE 55904 Rochester MN United States usa List(List(University Of Minnesota, 659), List(Graduate School Of The University Of Minnesota, 252), List(Univ. Minnesota, 175), List(University Of Minnesota Rochester, 91), List(University Of Minnesota-rochester, 25), List(Is A Part Of The Graduate School Of The University Of Minnesota, 21), List(The Mayo Foundation Is A Part Of The Graduate School Of The University Of Minnesota, 20), List(The University Of Minnesota., 10), List(The University Of Minnesota, 10), List((university Of Minnesota), 9)) r.umn.edu univ null null 60000209 118493055 Department of Immunology and Carole 60000209 UConn Health 60000209 UConn Health UConn Health 263 Farmington Avenue 06030-0002 Farmington CT United States usa List(List(University Of Connecticut Health Center, 18259), List(Univ. Of Connecticut Health Center, 5227), List(Uconn Health, 1741), List(Univ. Connecticut Hlth Cent., 1150), List(University Of Connecticut Health, 585), List(The University Of Connecticut Health Center, 401), List(Uconn Health Center, 331), List(Connecticut University Health Center, 220), List(University Of Connecticut Health Center Farmington, 182), List(Univ. Connecticut Health Cent., 176), List(University Of Connecticut Medical Center, 154)) uchc.edu meds null null 60000209 124587284 Molecular Cardiology Laboratory 60000209 UConn Health 60000209 UConn Health UConn Health 263 Farmington Avenue 06030-0002 Farmington CT United States usa List(List(University Of Connecticut Health Center, 18259), List(Univ. Of Connecticut Health Cen

In [0]:
affiliation_final_data = merge_final.drop('key','afid','preferred_name','name_variant').withColumnRenamed("afid_final",'afid').withColumnRenamed("preferred_name_final",'preferred_name')
#display(affiliation_final_data)

In [0]:
print(tablename_ipr)

ipr_20220901


In [0]:
affiliation_final_data.write.option("header", "true").csv('s3://elsevier-fcads-icsrlab-databricks/custom/proj_030_facmob/aff_parent_final.csv')

In [0]:
read_test = (
    spark.read.format("csv")
    .option("header", "true")
    .load(
        "s3://elsevier-fcads-icsrlab-databricks/custom/proj_030_facmob/aff_parent_final.csv"
    )
)
display(read_test.sort('afid'))

afid preferred_name parent_final parent_preferred_name_final sort_name address_part postal_code city state country country_tag org_domain org_type parent parent_preferred_name 100242043 Department of Pharmacology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242044 Department of Pathology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242045 Dept. of Biochemistry and Biophysics 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242046 Department of Biology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242047 Department of Chemistry 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242048 Department of Microbiology and Immunology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242049 Department of Physics 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242050 Department of Radiology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242051 Division of Nephrology and Hypertension 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242052 Department of Surgery 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242053 Department of Biostatistics 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242054 Department of Medicine 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242055 Department of Rheumatology 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242059 Department of Physics and Astronomy 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242060 Department of Marine Sciences 60025111 The University of North Carolina at Chapel Hill The University of North Carolina at Chapel Hill Jackson Hall, 153A Country Club Road 27514-4105 Chapel Hill NC United States usa unc.edu univ null null 100242061 Department of Psychology 60025111 The University of North Carolina at Chapel Hill The University of N

In [0]:
display(read_test.groupBy('parent_final','parent_preferred_name_final').count().sort('count'))

parent_final parent_preferred_name_final count 109940322 Field Diagnostic Services Inc. 1 109556369 T. Y. Lin and Associates 1 113192700 Axum Design and Engineering Corporation 1 119601939 Fototerra group 1 109549804 H.M. Prison 1 109583589 K2 Advisors 1 122535957 The Helene Fuld Health Trust National Institute for Evidence-Based Practice & Healthcare 1 60009853 Klein Associates Incorporated 1 123625184 Kedren Community Mental Health Center in South Central Los Angeles 1 109584003 Formerly of Blue Cross Blue Shield of North Carolina (RDP) 1 113193416 Arcadis-Malcolm Pirnie 1 112176008 Video Products Group, Inc. 1 109550427 North Carolina Mutual Life Insurance Company 1 112293495 Biomedical Instrumentsans and Devices 1 113273957 ACP Consultant Inc. 1 60074194 Otis Health Care Center 1 110004135 Lead Horse Technologies, Inc 1 119385762 Michigan Dep of Transportation 1 113521637 Ashe County 1 112447811 Physiometrex 1 109662294 Nanosonix Inc. 1 60078037 Agitar Software, Inc. 1 122274324 Psychiatric Clinic 1 112487269 AS and M, Inc. 1 60075789 Cerac-Pure Incorporated 1 60096157 Proton Labs, Inc. 1 113651972 Metropolitan Transportation Commission 1 112495594 Technol. Plan. and Integration Group 1 109669959 Singer Partners, LLC 1 100367447 SSD Engineering Consultants, Inc 1 60078052 Cambridge Management Group 1 112620403 Priest and Associates Consulting 1 123606451 Martin Marettia Aerospace 1 100402137 Center on Education Policy 1 113673430 Validation 1 112638059 James Madison College of Business 1 60074255 GSI Technologies, LLC 1 100446057 Vision Inspection Technology LLC 1 60090903 Poet LLC 1 112748912 Mayor's Office of New Urban Mechanics 1 110006323 Tetra Tech Sciences 1 100447405 Wellford & Nalven Inc 1 113741412 Space and Directed Energy Division 1 112782263 Lucas-Milhaupt 1 109880862 American Federation for Medical Research 1 100458513 Wildwood Medical Center 1 60101328 Community Health and Social Services Center, Inc 1 112786044 Carver Geologic, Inc. 1 60088254 BioTraces, Inc. 1 100458535 Keenan and Associates 1 113775192 Vacuum Technology, Inc. 1 112831723 Falmouth Osteopathy and Acupuncture, LLC in Falmouth 1 60077608 John H. Van Drie Research LLC 1 100486064 Telmos Inc 1 100345254 Ctr. for Backyard Astrophys. (East) 1 112893091 WesDyne International, LLC 1 110106094 Brookhart Enterprises LLC 1 100490254 SCREENING FOR MENTAL HEALTH, INC. 1 113802049 Tavernier Science Center 1 112922920 World Federation for Mental Health 1 109965440 PVI 1 100514955 Allergy and Asthma Center 1 100364290 Quality Technology Co. 1 112928342 Synergic Laboratories 1 113158601 Face Center Los Angeles 1 100526846 Cooper Electronic Technologies 1 113818812 Division of Bird Habitat Conservation 1 112928936 Commonfund Institute 1 60100314 VGO Associates 1 100539808 Brooktrout Technology, Inc. 1 100421217 Technol. and Devices Intl., Inc. 1 112949028 Jesuit School of Theology at Berkeley and the Graduate Theological Union 1 113173230 Lidar Pacific Corporation 1 100575087 Archaeo-Physics, LLC 1 113829124 GAO Consulting Services 1 112997377 U.S. Army Medical Research Laboratory Fort Knox 1 109985746 Centre for Advanced Imaging 1 100591062 Delta Faucet Company 1 100439723 OncorMed Inc. 1 113154577 Fast Forward, LLC 1 100346981 Transcultural C.A.R.E. Associates 1 100603145 LifeCenter Northwest 1 113892082 Radiabeam Techologies Ltd. 1 113176416 Oklahoma Natural Gas 1 100337928 Plasma-Therm LLC 1 100611015 Metron Optics Inc 1 100465747 Madrona Medical Group 1 113176446 Geochimica 1 113182565 Sen Francisco County Transportation Authority 1 100638184 SAI Consulting Engineers, Inc. 1 113908707 Surgical Health Collective 1 113178275 Denovo Biotechnology 1 110067615 Catholic Health Services of Long Island 1 100648170 Bipolar Disord. Clin. and Res. Prog. 1 100488287 Safematic Inc 1 113242347 ONEOK Energy Group 1 100372535 MedFlight 1 100661759 Nursing Solutions Consultants, LLC 1 113929147 Penn State's Capital College 1 113300255 Northside Family Medicine in Albuque

In [0]:
display(read_test.select('afid','preferred_name').subtract(read_test.select('parent_final','parent_preferred_name_final')))

afid preferred_name 100252848 Section of Cardiology 100254303 Department of Chemistry 100254840 Department of Pharmacology 100255963 School of Public Health 100256883 Division of Pediatric Cardiology 100260086 Department of Obstetrics and Gynecology 100261364 Department of Nutrition 100271534 Laboratory of Molecular Genetics 100276588 Department of Otorhinolaryngology 100278891 Department of Psychology 100284727 Dept. Pediat. 100292876 Department of Pharmacology 100294451 Laboratory of Molecular Biology 100296719 Department of Orthopaedics 100299158 Department of Pharmacy 100307090 Department of Pathology 102155033 Program Res. Unit. 102175387 Department of Orthopaedic Surgery 102177114 SW. Washington Perinatal Services 102192499 GEOMET Technologies Inc 102203195 Sacramento Division 102222640 Department of Biology 102227082 Center for Biological Conservation 102241638 Department of Obstetrics and Gynecology 102249064 Gastroenterology Section 102267663 Fam. Pract. Cent. 102299101 Division of Pulmonary, Critical Care and Internal Medicine 102301254 Energy Science Lab Inc 102331099 Department of Surgery 102364733 Division of Experimental Hematology 102369707 Development Systems Group B301 102381371 Department of Botany 102391533 Wilder Research Center 102432426 Ment. Hlth Serv. Deaf 102445625 Department of Chemistry 102469971 Hardware Engineering 102470370 School of Nursing 102508906 Sinus and Nasal Institute of Florida 102514977 Department of Pediatric Dentistry 102524789 Laboratory of Neurosciences 102528263 United States Fish and Wildlife Service 102554358 Department of Internal Medicine 102583170 Department of Research and Development 102584718 U.S. Geolodical Survey 102591841 Siemens Components Division 102595352 Occupational and Radiation Medicine 102614890 Department of Economics 102616848 Department of Medicine 102616940 Dept. Radiol. Int. Med. 102627817 Environm Criteria Assessment Office 102629659 Geriatrics Research Laboratory 102638021 Social Service 102642918 Departments of Veterinary Anatomy, Physiology and Cell Biology 102646400 Department of Radiology 102671158 Department of Chemistry 102678045 Department of Molecular and Medical Pharmacology 102684465 Department of Research 102744169 Group Advancem. Psychiat. 102744353 Professional Office Building 102747859 IML Technology Inc 102753653 Crystal Clinic 102758198 Fluid-Ionic Syst. Oper. 102760988 Lab. of Devtl. Biology and Repair 102767991 Westerville Fam. Consultation Center 102769003 Ohio Department of Education 102769007 Lettermen Army Medical Center 102783064 Legal Services for Children 102784309 Kentucky Dept. for Public Health 102817804 Dept of Civil and Environmental 102832836 Selspot Division 102842368 Los Angeles Psychiat. Serv. 102859197 Department of Radiology 102879025 Coll of Technology at Utica 102884648 Exploration Office 102929258 Wisconsin Department 102935147 Food Chemistry and Packaging Department 102959140 Patient Safety Network 102965022 Department of Pathology 102967655 Vineland Department of Health 102989865 Seawater Systems Design 103000267 Texas Department of Transportation 103016696 Dept. of Compar. Military Studies 103027802 College of Education and Adjunct 103037217 Department of Management 103044975 School of Nursing 103044989 Department of Research 103046544 Department of Molecular Biology 103046860 Hebrew Home/Hospital 103060216 Aerospace Mechanics Division 103063698 Sect. Aller. Clin. Immunol. 103063982 Division of Engineering 103072575 Stat. Lab. Educ. Psychol. Msrmt. 103073015 U. States Army Engineer Res. and D. 103090996 Department of Biology and Center for Disease Ecology 103098132 International Programs 103108807 Fixed Wing Systems Development 103109040 Life Sciences 103111847 Department of Otolaryngology, Division Head and Neck Surgery 103117247 PMNU Department 103120290 Ergonomics Department 103123641 Government Department 103125316 Dept. of Urol. and Geriatric Med. 103125879 Adolescent Medicine 103134890 Materials Science Labo

In [0]:
read_test.select('afid','preferred_name').subtract(read_test.select('parent_final','parent_preferred_name_final')).count()

Out[12]: 1538623